In [1]:
import os, sys
import numpy as np
import pandas as pd
import json
pd.options.mode.chained_assignment = None

import plotly.graph_objects as go
import plotly.io as pio
import plotly.express as px
from plotly.subplots import make_subplots
from unicodeit import replace as tex_to_unis
# sys.path.append("C:/Users/rurur/Desktop/p/python/plotly")
# import plotly_setup

In [23]:
result_files = os.listdir("./results")
result_titles = sorted(set([f.rstrip("full_.txt") for f in result_files]))
result_titles[0], result_titles[2] = result_titles[2], result_titles[0]
print(*result_files)
print(*result_titles)

CPython-3.11.txt CPython-3.11_full.txt CPython-3.9.txt CPython-3.9_full.txt Pyodide.txt PyPy-3.9-v7.3.13.txt PyPy-3.9-v7.3.13_full.txt Xeus.txt
PyPy-3.9-v7.3.13 CPython-3.9 CPython-3.11 Pyodide Xeus


In [24]:
df = pd.DataFrame()
funcs = ["time_with_types", "time_no_types", "time_np"]
funcs_titles = [f.lstrip("time_") for f in funcs]
funcs_titles[-1] = "numpy"
for rtitle in result_titles:
    with open(f"results/{rtitle}.txt", "r", encoding="utf-8") as f:
        result = json.load(f)
    result_df = pd.DataFrame(dict(
        interpreter=result["interpreter"],
        time=[result[func] for func in funcs],
        funcs=funcs_titles,
        test_mode="func"
    ))
    df = pd.concat([df, result_df], ignore_index=True)

    fname_full_time = f"{rtitle}_full.txt"
    if fname_full_time in result_files:
        with open(f"results/{fname_full_time}", "r", encoding="utf-8") as f:
            times = [float(line) for line in f.readlines()]
        result_df = pd.DataFrame(dict(
            interpreter=result["interpreter"],
            time=times,
            funcs=funcs_titles,
            test_mode="full"
        ))
        df = pd.concat([df, pd.DataFrame(result_df)], ignore_index=True)


In [25]:
df

interpreter       time       funcs test_mode
0   PyPy-3.9-v7.3.13   0.099364  with_types      func
1   PyPy-3.9-v7.3.13   0.109924    no_types      func
2   PyPy-3.9-v7.3.13   3.676712       numpy      func
3   PyPy-3.9-v7.3.13   5.319000  with_types      full
4   PyPy-3.9-v7.3.13   3.638000    no_types      full
5   PyPy-3.9-v7.3.13  14.639000       numpy      full
6        CPython-3.9   1.445288  with_types      func
7        CPython-3.9   1.476920    no_types      func
8        CPython-3.9   1.407270       numpy      func
9        CPython-3.9   2.242000  with_types      full
10       CPython-3.9   1.502000    no_types      full
11       CPython-3.9   1.986000       numpy      full
12      CPython-3.11   0.820678  with_types      func
13      CPython-3.11   0.856216    no_types      func
14      CPython-3.11   1.202004       numpy      func
15      CPython-3.11   1.630000  with_types      full
16      CPython-3.11   1.166000    no_types      full
17      CPython-3.11   1.675000       numpy      full
18           piodide   1.785000  with_types      func
19           piodide   1.681000    no_types      func
20           piodide   2.833000       numpy      func
21              Xeus   1.155519  with_types      func
22              Xeus   1.038669    no_types      func
23              Xeus   1.272793       numpy      func

In [85]:
fig = px.bar(df,
    x="interpreter",
    y="time",
    facet_col="funcs",
    facet_row="test_mode",
    facet_row_spacing=0.15,
    facet_col_spacing=0.03,
    labels=dict(time="Time, s")
).update_layout(
    width=800, height=620,
    margin=dict(b=10, t=20),
    # title=dict(text="Results of Testing"),
    font=dict(size=13)
).update_yaxes(
    matches=None,
).update_yaxes(
    # showticklabels=True,
    row=1,
    range=(0, 16)
).update_yaxes(
    # showticklabels=True,
    row=2,
    range=(0, 4)
).update_xaxes(
    matches=None,
    showticklabels=True,
    title=None
).for_each_annotation(
    lambda a: a.update(text=a.text.split("=")[-1])
)
fig.write_image("result.png", scale=2.5)
# fig.layout.yaxis.matches = 'y'
# fig.layout.yaxis1.matches = 'y1'
fig.show()